In [1]:
# Data 
import matplotlib.pyplot as plt
import sys
import numpy as np
# Dataset
from keras.datasets import mnist
# ML
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation
from keras.layers.advanced_activations import LeakyReLU
from keras.models import Sequential, Model
from keras.optimizers import Adam

Using TensorFlow backend.


In [2]:
class GAN():
    def __init__(self):
        optimizer = Adam(0.0002, 0.5)
        # image pixel density
        self.img_rows = 28
        self.img_cols = 28
        self.channels = 1
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        # setting the input noise size
        self.latent_dim = 100

        # creating/compiling the discriminator
        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])
        # can't train discriminator
        self.discriminator.trainable = False
        
        # creating/compiling the generator
        self.generator = self.build_generator()
        # generated image
        z = Input(shape=(self.latent_dim,))
        img = self.generator(z)
        
        # descriminator decision
        validity = self.discriminator(img)
        
        # combine models and set loss and optimizer
        self.combined = Model(z, validity)
        self.combined.compile(loss='binary_crossentropy', optimizer=optimizer)
        

    def build_generator(self):
        alpha = 0.2
        momentum = 0.8
        neurons = 256
        #activation function
        activation = LeakyReLU(alpha=alpha)
        
        # set the model
        model = Sequential()
        # input layer and noise
        model.add(Dense(neurons, input_dim=self.latent_dim))
        model.add(activation)
        model.add(BatchNormalization(momentum=momentum))
        # layer 2
        model.add(Dense(neurons*2))
        model.add(activation)
        model.add(BatchNormalization(momentum=momentum))
        # layer 3
        model.add(Dense(neurons*(2**2)))
        model.add(activation)
        model.add(BatchNormalization(momentum=momentum))
        # output layer
        model.add(Dense(np.prod(self.img_shape), activation='tanh'))
        model.add(Reshape(self.img_shape))
        
        model.summary()
        
        # image created
        noise = Input(shape=(self.latent_dim,))
        img = model(noise)
        
        return Model(noise, img)
    
    
    def build_discriminator(self):
        neurons = 256
        alpha = 0.2

        model = Sequential()
        # layer 1
        model.add(Flatten(input_shape=self.img_shape))
        model.add(Dense(neurons * 2))
        model.add(LeakyReLU(alpha=alpha))
        # layer 2
        model.add(Dense(neurons * 2))
        model.add(LeakyReLU(alpha=alpha))
        # output layer
        model.add(Dense(1, activation='sigmoid'))
        model.summary()
        img = Input(shape=self.img_shape)
        # discriminator's guess
        validity = model(img)

        return Model(img, validity)


    def train(self, epochs, batch_size=128, sample_interval=50):
        # loading the dataset
        (X_train, _), (_, _) = mnist.load_data()
        # rescaling training images
        X_train = X_train / 127.5 - 1.
        X_train = np.expand_dims(X_train, axis=3)
        # labels
        valid = np.ones((batch_size, 1))
        fake = np.zeros((batch_size, 1))

        for epoch in range(epochs):
            # getting random sample
            idx = np.random.randint(0, X_train.shape[0], batch_size)
            imgs = X_train[idx]
            # selecting random noiseusing the size of the latent dimensions
            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
            # generating an image with random noise
            gen_imgs = self.generator.predict(noise)
            # calculating losses
            d_loss_real = self.discriminator.train_on_batch(imgs, valid)
            d_loss_fake = self.discriminator.train_on_batch(gen_imgs, fake)
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)

            # generator training based on discrimimator label
            noise = np.random.normal(0, 1, (batch_size, self.latent_dim))
            g_loss = self.combined.train_on_batch(noise, valid)

            # printing progress
            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))
            if epoch % sample_interval == 0:
               self.sample_images(epoch)
        
        
    def sample_images(self, epoch):
        r, c = 5, 5
        noise = np.random.normal(0, 1, (r * c, self.latent_dim))
        gen_imgs = self.generator.predict(noise)
        gen_imgs = 0.5 * gen_imgs + 0.5
        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt, :,:,0], cmap='gray')
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("images/%d.png" % epoch)
        plt.close()

In [3]:
if __name__ == '__main__':
    gan = GAN()
    gan.train(epochs=100000, batch_size=132, sample_interval=10000)

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_1 (Flatten)          (None, 784)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 512)               401920    
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 512)               262656    
_________________________________________________________________
leaky_re_lu_2 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 513       
Total params: 665,089
Trainable params: 665,089
Non-trainable params: 0
________________________________________________

C:\ProgramData\Anaconda3\lib\site-packages\keras\engine\training.py:297: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


0 [D loss: 0.706164, acc.: 52.65%] [G loss: 0.740059]


C:\ProgramData\Anaconda3\lib\site-packages\keras\engine\training.py:297: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


1 [D loss: 0.370732, acc.: 86.74%] [G loss: 0.762851]
2 [D loss: 0.337256, acc.: 85.98%] [G loss: 0.853150]
3 [D loss: 0.321251, acc.: 89.02%] [G loss: 0.926371]
4 [D loss: 0.293253, acc.: 95.08%] [G loss: 1.111441]
5 [D loss: 0.261219, acc.: 97.73%] [G loss: 1.298086]
6 [D loss: 0.219445, acc.: 99.62%] [G loss: 1.550982]
7 [D loss: 0.168681, acc.: 100.00%] [G loss: 1.837126]
8 [D loss: 0.134692, acc.: 100.00%] [G loss: 1.994565]
9 [D loss: 0.108493, acc.: 100.00%] [G loss: 2.235704]
10 [D loss: 0.086694, acc.: 100.00%] [G loss: 2.409149]
11 [D loss: 0.072195, acc.: 100.00%] [G loss: 2.534966]
12 [D loss: 0.059459, acc.: 100.00%] [G loss: 2.691722]
13 [D loss: 0.056105, acc.: 100.00%] [G loss: 2.807470]
14 [D loss: 0.046406, acc.: 100.00%] [G loss: 2.929802]
15 [D loss: 0.040584, acc.: 100.00%] [G loss: 2.941215]
16 [D loss: 0.038968, acc.: 100.00%] [G loss: 3.011178]
17 [D loss: 0.037708, acc.: 100.00%] [G loss: 3.120073]
18 [D loss: 0.034752, acc.: 100.00%] [G loss: 3.197263]
19 [D l

...

99317 [D loss: 0.437607, acc.: 78.41%] [G loss: 1.467688]
99318 [D loss: 0.484489, acc.: 77.65%] [G loss: 1.509361]
99319 [D loss: 0.510079, acc.: 73.86%] [G loss: 1.715437]
99320 [D loss: 0.517754, acc.: 73.11%] [G loss: 1.358460]
99321 [D loss: 0.492750, acc.: 76.89%] [G loss: 1.540846]
99322 [D loss: 0.513916, acc.: 70.45%] [G loss: 1.446681]
99323 [D loss: 0.534377, acc.: 76.52%] [G loss: 1.490929]
99324 [D loss: 0.479246, acc.: 77.27%] [G loss: 1.581937]
99325 [D loss: 0.544902, acc.: 72.35%] [G loss: 1.558601]
99326 [D loss: 0.464412, acc.: 77.27%] [G loss: 1.509309]
99327 [D loss: 0.455203, acc.: 75.00%] [G loss: 1.579514]
99328 [D loss: 0.500124, acc.: 76.52%] [G loss: 1.573600]
99329 [D loss: 0.519482, acc.: 70.08%] [G loss: 1.646042]
99330 [D loss: 0.523418, acc.: 73.48%] [G loss: 1.560495]
99331 [D loss: 0.465323, acc.: 76.89%] [G loss: 1.506321]
99332 [D loss: 0.452624, acc.: 79.17%] [G loss: 1.592350]
99333 [D loss: 0.495147, acc.: 79.17%] [G loss: 1.520574]
99334 [D loss:

99459 [D loss: 0.504091, acc.: 72.73%] [G loss: 1.457639]
99460 [D loss: 0.447650, acc.: 79.92%] [G loss: 1.510623]
99461 [D loss: 0.463635, acc.: 77.65%] [G loss: 1.655731]
99462 [D loss: 0.446636, acc.: 77.65%] [G loss: 1.686780]
99463 [D loss: 0.499584, acc.: 72.35%] [G loss: 1.546145]
99464 [D loss: 0.499846, acc.: 76.14%] [G loss: 1.427291]
99465 [D loss: 0.512389, acc.: 75.76%] [G loss: 1.508045]
99466 [D loss: 0.522467, acc.: 70.45%] [G loss: 1.483114]
99467 [D loss: 0.457763, acc.: 78.41%] [G loss: 1.546100]
99468 [D loss: 0.562912, acc.: 69.70%] [G loss: 1.606110]
99469 [D loss: 0.503346, acc.: 74.24%] [G loss: 1.716889]
99470 [D loss: 0.492312, acc.: 78.03%] [G loss: 1.514665]
99471 [D loss: 0.487081, acc.: 74.62%] [G loss: 1.425393]
99472 [D loss: 0.557917, acc.: 69.32%] [G loss: 1.566288]
99473 [D loss: 0.536274, acc.: 74.62%] [G loss: 1.474175]
99474 [D loss: 0.478081, acc.: 78.03%] [G loss: 1.450184]
99475 [D loss: 0.472055, acc.: 76.89%] [G loss: 1.529348]
99476 [D loss:

99601 [D loss: 0.521338, acc.: 74.24%] [G loss: 1.481211]
99602 [D loss: 0.522092, acc.: 76.52%] [G loss: 1.511166]
99603 [D loss: 0.531110, acc.: 73.86%] [G loss: 1.349942]
99604 [D loss: 0.525100, acc.: 72.35%] [G loss: 1.687766]
99605 [D loss: 0.473440, acc.: 78.41%] [G loss: 1.747568]
99606 [D loss: 0.530822, acc.: 72.73%] [G loss: 1.621516]
99607 [D loss: 0.501895, acc.: 74.62%] [G loss: 1.576554]
99608 [D loss: 0.493020, acc.: 75.38%] [G loss: 1.596598]
99609 [D loss: 0.456772, acc.: 76.14%] [G loss: 1.506244]
99610 [D loss: 0.498858, acc.: 76.14%] [G loss: 1.646941]
99611 [D loss: 0.482317, acc.: 72.73%] [G loss: 1.523537]
99612 [D loss: 0.506367, acc.: 75.00%] [G loss: 1.412381]
99613 [D loss: 0.476263, acc.: 78.41%] [G loss: 1.559767]
99614 [D loss: 0.478579, acc.: 78.79%] [G loss: 1.564117]
99615 [D loss: 0.477337, acc.: 79.55%] [G loss: 1.474093]
99616 [D loss: 0.502693, acc.: 75.00%] [G loss: 1.542341]
99617 [D loss: 0.541933, acc.: 72.73%] [G loss: 1.708333]
99618 [D loss:

99744 [D loss: 0.463396, acc.: 78.41%] [G loss: 1.571742]
99745 [D loss: 0.505009, acc.: 74.62%] [G loss: 1.601349]
99746 [D loss: 0.477492, acc.: 79.17%] [G loss: 1.546063]
99747 [D loss: 0.492104, acc.: 78.03%] [G loss: 1.472792]
99748 [D loss: 0.488632, acc.: 78.41%] [G loss: 1.507345]
99749 [D loss: 0.556312, acc.: 69.32%] [G loss: 1.597571]
99750 [D loss: 0.497014, acc.: 76.52%] [G loss: 1.527578]
99751 [D loss: 0.483013, acc.: 75.76%] [G loss: 1.589368]
99752 [D loss: 0.481820, acc.: 75.00%] [G loss: 1.521175]
99753 [D loss: 0.508502, acc.: 77.27%] [G loss: 1.580206]
99754 [D loss: 0.514336, acc.: 75.00%] [G loss: 1.782578]
99755 [D loss: 0.504684, acc.: 73.11%] [G loss: 1.617491]
99756 [D loss: 0.541512, acc.: 71.97%] [G loss: 1.637427]
99757 [D loss: 0.523604, acc.: 71.97%] [G loss: 1.644023]
99758 [D loss: 0.490105, acc.: 76.52%] [G loss: 1.596871]
99759 [D loss: 0.520637, acc.: 77.27%] [G loss: 1.635360]
99760 [D loss: 0.507831, acc.: 75.76%] [G loss: 1.497189]
99761 [D loss:

99886 [D loss: 0.483389, acc.: 77.27%] [G loss: 1.618800]
99887 [D loss: 0.478324, acc.: 77.65%] [G loss: 1.480853]
99888 [D loss: 0.482333, acc.: 77.27%] [G loss: 1.634780]
99889 [D loss: 0.476591, acc.: 77.65%] [G loss: 1.526871]
99890 [D loss: 0.511047, acc.: 71.21%] [G loss: 1.680615]
99891 [D loss: 0.539565, acc.: 73.48%] [G loss: 1.540982]
99892 [D loss: 0.455685, acc.: 78.03%] [G loss: 1.458514]
99893 [D loss: 0.464859, acc.: 77.65%] [G loss: 1.633889]
99894 [D loss: 0.478717, acc.: 76.14%] [G loss: 1.680357]
99895 [D loss: 0.509813, acc.: 75.00%] [G loss: 1.617059]
99896 [D loss: 0.491395, acc.: 77.27%] [G loss: 1.533889]
99897 [D loss: 0.493962, acc.: 76.89%] [G loss: 1.455440]
99898 [D loss: 0.523622, acc.: 74.24%] [G loss: 1.683229]
99899 [D loss: 0.451810, acc.: 78.41%] [G loss: 1.534401]
99900 [D loss: 0.485498, acc.: 75.38%] [G loss: 1.639433]
99901 [D loss: 0.448895, acc.: 80.30%] [G loss: 1.557058]
99902 [D loss: 0.526796, acc.: 74.24%] [G loss: 1.584555]
99903 [D loss: